# Proyecto Statistical Learning

## Problema 1 Music Year Prediction

### 0. Importación de Librerías
Para la transformación de los datos, así como para el entrenamiento de los modelos y la visualización de los resultados, se importan las siguientes librerías:

In [1]:
!pip install ydata-profiling

In [1]:
import pandas as pd
import numpy as np
import random

import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

from ydata_profiling import ProfileReport

import tensorflow as tf

from keras.models import Sequential
from keras.layers import Activation, Dropout, Flatten, Dense, Input
from keras import backend as K
from keras import applications, models

from sklearn.metrics import classification_report, confusion_matrix
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import make_column_transformer
from sklearn.compose import make_column_selector
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.preprocessing import StandardScaler, PolynomialFeatures
from sklearn.preprocessing import OneHotEncoder, OrdinalEncoder
from sklearn.linear_model import Lasso, Ridge
from sklearn.preprocessing import MinMaxScaler
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.compose import ColumnTransformer, make_column_selector
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score
from sklearn.ensemble import RandomForestRegressor
from sklearn.feature_selection import SelectFromModel
from sklearn.feature_selection import SelectKBest, f_regression

import optuna

#Librerías extras
import itertools

print('Tensorflow version:', tf.__version__)

Tensorflow version: 2.13.0


In [2]:
file = 'C:/Users/danie/OneDrive - Universidad de los andes/Doctorado/Statistical learning/Proyecto/trainReg.txt'
data = pd.read_csv(file)
data.head()

V1        V2       V3  V4        V5        V6       V7        V8  \
0  2013  44.81144  0.83826   0   7.91314  10.94148 -0.04547 -15.16332   
1  1998  41.99180  7.99976   0  64.26707  16.54115 -9.28737 -40.73524   
2  1998  42.19196  2.23111   0  65.07719  24.99746  1.76100   6.66573   
3  1998  39.28634 -1.85716   0  91.04190   9.08333  0.08502  -5.59216   
4  1998  40.36025  2.94918   0  53.83723  13.71369 -8.21964 -40.21636   

         V9       V10  ...       V82        V83        V84        V85  \
0 -10.47324  14.17212  ...  -8.44873 -230.30484  -40.94698   48.20025   
1  33.60440   9.18802  ...  18.68972  -44.06062   52.37792   81.36093   
2   3.45778 -24.42779  ...  -3.69878 -118.95712   54.15529  -23.32168   
3  65.62463   8.33105  ...  20.89044  -18.53135  176.09769  351.33669   
4  21.22366  17.16742  ...  19.91979   34.59026  -69.83720  102.31946   

        V86        V87        V88       V89        V90       V91  
0  -0.28694  155.76251  -56.23579  13.62599  123.92018  10.02845  
1 -14.81111  151.66273 -120.61213  10.57519   -3.21078  -1.07438  
2  -9.65067  -83.83055 -141.17594   7.33084 -275.69714   2.35522  
3   3.44682  121.69156 -270.43989  12.51659 -140.88884  -0.23476  
4   8.08807  135.08089 -153.02327   4.09207  -68.33046  -6.19159  

[5 rows x 91 columns]

In [6]:
ProfileReport(data,minimal=True)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [3]:
X_train, y_train = data.drop(['V1', 'V4'], axis = 1), data['V1']
X_train

V2       V3        V5        V6       V7        V8        V9  \
0      44.81144  0.83826   7.91314  10.94148 -0.04547 -15.16332 -10.47324   
1      41.99180  7.99976  64.26707  16.54115 -9.28737 -40.73524  33.60440   
2      42.19196  2.23111  65.07719  24.99746  1.76100   6.66573   3.45778   
3      39.28634 -1.85716  91.04190   9.08333  0.08502  -5.59216  65.62463   
4      40.36025  2.94918  53.83723  13.71369 -8.21964 -40.21636  21.22366   
...         ...      ...       ...       ...      ...       ...       ...   
77774  33.76706 -3.80678  -1.44169  23.78801  5.01781   1.58966 -25.02281   
77775  25.77805  2.41861   5.96418  -8.43658 -1.36182   2.51784 -18.57770   
77776  24.78656  1.36415  34.13329  34.32996 -0.95170  75.33572 -28.59028   
77777  39.67698  3.65167  34.04925  -0.68467 -2.13911  -5.70096 -10.57862   
77778  44.44499  8.89481  48.99411  15.83343  5.00566 -23.89831 -21.12626   

            V10       V11        V12  ...       V82        V83        V84  \
0      14.17212  10.57382  -11.21128  ...  -8.44873 -230.30484  -40.94698   
1       9.18802  -6.79144   44.21327  ...  18.68972  -44.06062   52.37792   
2     -24.42779 -18.45069  233.16766  ...  -3.69878 -118.95712   54.15529   
3       8.33105  11.70269   79.90772  ...  20.89044  -18.53135  176.09769   
4      17.16742   0.14463   72.23955  ...  19.91979   34.59026  -69.83720   
...         ...       ...        ...  ...       ...        ...        ...   
77774  25.90399  19.87408  -21.41492  ... -36.84706 -637.31267 -174.93600   
77775 -25.69885   9.97971 -100.96885  ...  27.76376  -44.59643 -116.15080   
77776 -31.86076  -4.06444  -53.17960  ...  33.73262 -206.05602   44.10029   
77777  -1.30048   9.85726    7.33263  ... -15.46611 -117.84462  139.93465   
77778 -12.13135  12.76931  -44.42589  ...  -9.07718 -623.88638  186.93061   

             V85       V86        V87        V88       V89         V90  \
0       48.20025  -0.28694  155.76251  -56.23579  13.62599   123.92018   
1       81.36093 -14.81111  151.66273 -120.61213  10.57519    -3.21078   
2      -23.32168  -9.65067  -83.83055 -141.17594   7.33084  -275.69714   
3      351.33669   3.44682  121.69156 -270.43989  12.51659  -140.88884   
4      102.31946   8.08807  135.08089 -153.02327   4.09207   -68.33046   
...          ...       ...        ...        ...       ...         ...   
77774  127.32951 -15.75226 -144.64697    6.53731   5.54065   193.68594   
77775  -34.33917   4.86612  141.37999  282.57252  23.32459   125.07389   
77776 -635.01673 -16.75481  114.74225 -192.79351  -4.44202  1457.72692   
77777   67.70637 -24.18488  -39.54694  185.26251  -1.37534   216.14774   
77778   -9.41335 -11.51320  137.13883  -80.15732  20.33014   106.69048   

            V91  
0      10.02845  
1      -1.07438  
2       2.35522  
3      -0.23476  
4      -6.19159  
...         ...  
77774  32.75930  
77775 -19.16268  
77776 -50.93615  
77777 -12.75066  
77778   6.68635  

[77779 rows x 89 columns]

In [5]:

# Creando el selector de características
selector = SelectKBest(score_func=f_regression, k=30)

# Ajustando el selector a los datos
X_selected = selector.fit_transform(X_train, y_train)

# Obteniendo los índices de las características seleccionadas
selected_indices = selector.get_support(indices=True)

# Obteniendo los nombres de las características seleccionadas
selected_features = X_train.columns[selected_indices]

print("Características seleccionadas:")
print(selected_features)


Características seleccionadas:
Index(['V2', 'V6', 'V9', 'V12', 'V15', 'V21', 'V22', 'V25', 'V26', 'V30',
       'V32', 'V34', 'V37', 'V39', 'V41', 'V42', 'V47', 'V48', 'V54', 'V58',
       'V60', 'V64', 'V68', 'V69', 'V70', 'V73', 'V74', 'V75', 'V79', 'V87'],
      dtype='object')


Modelos posibles music Year Prediction
1. Regresion lineal
2. Ridge o lasso 
3. PCA
5. PLSR
4. k-vecinos
6. Regresion por kernel
7. Regresion splines
8. MARS
9. GAMS
10. Smoothing splines
11. Random forest
12. Redes neuronales


### Regresion lasso

In [5]:
LassoModel = Lasso(alpha=100)
LassoModel.fit(X_train, y_train)
print('Coefficients: ', LassoModel.coef_)
print('Intercept: ',LassoModel.intercept_)

Coefficients:  [ 0.          0.         -0.          0.         -0.         -0.
 -0.         -0.          0.         -0.          0.          0.
  0.00049017 -0.0005141   0.00011059  0.         -0.         -0.
  0.00196572 -0.00051495 -0.          0.         -0.          0.
 -0.00013431  0.          0.          0.          0.         -0.
 -0.         -0.          0.         -0.         -0.         -0.00045475
  0.00098275  0.00085885 -0.00259635 -0.          0.         -0.
  0.          0.         -0.          0.00100796 -0.00080934 -0.
 -0.         -0.         -0.          0.         -0.         -0.
 -0.         -0.00118882  0.         -0.00147608 -0.         -0.
 -0.         -0.          0.         -0.         -0.         -0.
  0.         -0.          0.          0.         -0.          0.
  0.          0.          0.         -0.         -0.0004588   0.
 -0.         -0.          0.          0.          0.          0.
 -0.          0.         -0.         -0.         -0.        ]
Inter

Asociar los coeficientes a los atributos

In [6]:
coef = dict(zip(X_train.columns, LassoModel.coef_))
for k,v in coef.items():
    print(f'{k} = {v:,.2f}')

V2 = 0.00
V3 = 0.00
V5 = -0.00
V6 = 0.00
V7 = -0.00
V8 = -0.00
V9 = -0.00
V10 = -0.00
V11 = 0.00
V12 = -0.00
V13 = 0.00
V14 = 0.00
V15 = 0.00
V16 = -0.00
V17 = 0.00
V18 = 0.00
V19 = -0.00
V20 = -0.00
V21 = 0.00
V22 = -0.00
V23 = -0.00
V24 = 0.00
V25 = -0.00
V26 = 0.00
V27 = -0.00
V28 = 0.00
V29 = 0.00
V30 = 0.00
V31 = 0.00
V32 = -0.00
V33 = -0.00
V34 = -0.00
V35 = 0.00
V36 = -0.00
V37 = -0.00
V38 = -0.00
V39 = 0.00
V40 = 0.00
V41 = -0.00
V42 = -0.00
V43 = 0.00
V44 = -0.00
V45 = 0.00
V46 = 0.00
V47 = -0.00
V48 = 0.00
V49 = -0.00
V50 = -0.00
V51 = -0.00
V52 = -0.00
V53 = -0.00
V54 = 0.00
V55 = -0.00
V56 = -0.00
V57 = -0.00
V58 = -0.00
V59 = 0.00
V60 = -0.00
V61 = -0.00
V62 = -0.00
V63 = -0.00
V64 = -0.00
V65 = 0.00
V66 = -0.00
V67 = -0.00
V68 = -0.00
V69 = 0.00
V70 = -0.00
V71 = 0.00
V72 = 0.00
V73 = -0.00
V74 = 0.00
V75 = 0.00
V76 = 0.00
V77 = 0.00
V78 = -0.00
V79 = -0.00
V80 = 0.00
V81 = -0.00
V82 = -0.00
V83 = 0.00
V84 = 0.00
V85 = 0.00
V86 = 0.00
V87 = -0.00
V88 = 0.00
V89 = -0.00
V9

Evaluación del modelo

In [7]:
y_pred = LassoModel.predict(X_train)
y_pred

array([2003.28593825, 2002.49000328, 2001.44790556, ..., 2005.29174468,
       2005.66775386, 2004.21218152])

Para determinar nuestro rendimiento, vamos a utilizar dos métricas, el $MSE$ y el $R^2$.

In [8]:
n,p = X_train.shape

print('------------ Regresión Lasso con entrenamiento------------')
print("Residual sum of squares (MSE): %.2f" % mean_squared_error(y_train,y_pred))
print("R2-score: %.5f" % r2_score(y_train, y_pred) )
print("Adj R2-score: %.5f" % ( 1-(1-r2_score(y_train, y_pred))*(n-1)/(n-p-1)) )

------------ Regresión Lasso con entrenamiento------------
Residual sum of squares (MSE): 111.56
R2-score: 0.04553
Adj R2-score: 0.04444


Ahora utilizaremos los datos de validación para ver el rendimiento del modelo.

In [9]:
file_val = 'C:/Users/danie/OneDrive - Universidad de los andes/Doctorado/Statistical learning/Proyecto/testReg.txt'
X_test = pd.read_csv(file_val)
X_test


Id        V2       V3  V4        V5        V6       V7        V8  \
0          1  35.74170  0.86615   0   1.44450 -13.87834 -9.57602   5.89475   
1          2  35.31664 -0.47799   0 -12.27958 -29.32847 -2.38610  -7.27386   
2          3  43.25032 -6.31920   0  -2.56469  -7.59368  2.12862  23.29535   
3          4  44.94220 -4.12303   0 -15.79205   7.15794  1.46007  -3.38280   
4          5  50.40813 -1.52061   0 -10.10142 -17.74876 -5.96768 -29.94136   
...      ...       ...      ...  ..       ...       ...      ...       ...   
18652  18653  47.13482  3.84421   0  10.65084   6.76621 -7.62802   3.94229   
18653  18654  44.88535  1.21785   0  21.46818   6.06535 -3.21715 -49.46917   
18654  18655  49.12753  0.02024   0  -2.47167  11.16809  6.98209 -31.67139   
18655  18656  47.07399 -2.12987   0  19.65870   7.44925  9.22878  -0.28598   
18656  18657  45.93657  0.16199   0 -19.49991  12.83200 -8.79991  17.32559   

             V9       V10  ...       V82        V83        V84        V85  \
0      -4.46036 -10.60501  ...  10.78210 -183.63792  131.18868   37.68626   
1      -1.87712  -3.74953  ...  53.92478 -238.77713  134.28149   81.19403   
2      -0.34225   4.48761  ...  40.95711 -269.59803   69.88747   29.65701   
3      -8.48270  12.69732  ...   0.81574 -243.09497   24.20334  -10.02719   
4     -11.84237   5.90144  ...  -3.58634  -61.67109   47.53814  139.04916   
...         ...       ...  ...       ...        ...        ...        ...   
18652 -17.54994  -1.50402  ...   6.79574   50.40788 -208.86022    4.07771   
18653  -4.24723 -11.95931  ...  23.74218   31.83756  100.18131   24.23003   
18654 -24.20034  -3.32383  ...  -3.44803   -5.25300  -70.27796  -19.94830   
18655   5.97625  -5.43954  ...   3.92133  143.43511   -1.45249  -24.09898   
18656 -35.85872 -15.51939  ...  21.18688 -110.63226 -101.11562 -189.47922   

            V86        V87        V88       V89        V90       V91  
0      -4.48926   10.98139  -48.14549  -7.27992  -54.52826   4.81414  
1      -4.81669  106.00178    3.34940   2.72328  156.94894  -8.44873  
2      -0.12854  106.92919  -62.86550  30.12278   24.39843 -10.68316  
3      19.25667   66.15602  -64.78646   9.09148   11.46055  -7.12136  
4       6.85904  -57.09356  -49.57683  -6.61453   22.55497  -4.39272  
...         ...        ...        ...       ...        ...       ...  
18652  22.98125    7.57026  -24.53948 -10.50575  -43.87160 -12.16460  
18653 -12.11153  -36.12918  -75.12454  -8.55251  -68.83852  16.46255  
18654  -6.54688   -8.89722 -183.92335  14.82729  192.20814  32.05995  
18655  -2.44389   45.49691   59.01571  -0.00247   79.83971   7.36172  
18656  -0.72287   76.50974 -162.09858  -9.29159    2.50809  -1.62172  

[18657 rows x 91 columns]

In [10]:
X_test = X_test.drop(['Id','V4'],axis=1)
y_pred2 = LassoModel.predict(X_test)
year_pred = np.round(y_pred2).astype(int)
year_pred

array([2004, 2001, 2002, ..., 2000, 2002, 2001])

In [11]:
df = pd.DataFrame({"Id": range(1, len(year_pred)+1), "Year":year_pred})
df

Id  Year
0          1  2004
1          2  2001
2          3  2002
3          4  2002
4          5  2003
...      ...   ...
18652  18653  2002
18653  18654  2002
18654  18655  2000
18655  18656  2002
18656  18657  2001

[18657 rows x 2 columns]

In [12]:
df.to_csv('Lasso sensillo.txt', sep='\t', index=False)

In [13]:
estimators = [
        ('polinomial',PolynomialFeatures()),
        ('regresion', Lasso()) 
    ]

pipe = Pipeline(estimators)

parameters = {
              'polinomial__degree':[2,3],
              'regresion__alpha': [0.01, 0.1, 1, 10, 100],
              }

grid_search = GridSearchCV(pipe, parameters, verbose=2, scoring='neg_mean_squared_error', cv=5)

In [14]:
grid_search.fit(X_train,y_train)

Fitting 5 folds for each of 10 candidates, totalling 50 fits


c:\Users\danie\anaconda3\Lib\site-packages\sklearn\linear_model\_coordinate_descent.py:628: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.221e+06, tolerance: 7.329e+02
  model = cd_fast.enet_coordinate_descent(


[CV] END ........polinomial__degree=2, regresion__alpha=0.01; total time= 9.6min


c:\Users\danie\anaconda3\Lib\site-packages\sklearn\linear_model\_coordinate_descent.py:628: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.186e+06, tolerance: 7.139e+02
  model = cd_fast.enet_coordinate_descent(


[CV] END ........polinomial__degree=2, regresion__alpha=0.01; total time= 9.5min


...

[CV] END .........polinomial__degree=2, regresion__alpha=100; total time= 6.2min


c:\Users\danie\anaconda3\Lib\site-packages\sklearn\linear_model\_coordinate_descent.py:628: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.522e+06, tolerance: 7.408e+02
  model = cd_fast.enet_coordinate_descent(


[CV] END .........polinomial__degree=2, regresion__alpha=100; total time= 6.2min
[CV] END ........polinomial__degree=3, regresion__alpha=0.01; total time=   0.0s
[CV] END ........polinomial__degree=3, regresion__alpha=0.01; total time=   0.0s
[CV] END ........polinomial__degree=3, regresion__alpha=0.01; total time=   0.0s
[CV] END ........polinomial__degree=3, regresion__alpha=0.01; total time=   0.0s
[CV] END ........polinomial__degree=3, regresion__alpha=0.01; total time=   0.0s
[CV] END .........polinomial__degree=3, regresion__alpha=0.1; total time=   0.0s
[CV] END .........polinomial__degree=3, regresion__alpha=0.1; total time=   0.0s
[CV] END .........polinomial__degree=3, regresion__alpha=0.1; total time=   0.0s
[CV] END .........polinomial__degree=3, regresion__alpha=0.1; total time=   0.0s
[CV] END .........polinomial__degree=3, regresion__alpha=0.1; total time=   0.0s
[CV] END ...........polinomial__degree=3, regresion__alpha=1; total time=   0.0s
[CV] END ...........polinomi

c:\Users\danie\anaconda3\Lib\site-packages\sklearn\model_selection\_validation.py:425: FitFailedWarning: 
25 fits failed out of a total of 50.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
20 fits failed with the following error:
Traceback (most recent call last):
  File "c:\Users\danie\anaconda3\Lib\site-packages\sklearn\model_selection\_validation.py", line 732, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "c:\Users\danie\anaconda3\Lib\site-packages\sklearn\base.py", line 1151, in wrapper
    return fit_method(estimator, *args, **kwargs)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\danie\anaconda3\Lib\site-packages\sklearn\pipeline.py", line 416, in fit
    Xt = self._fit(X, y, **fi

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('polinomial', PolynomialFeatures()),
                                       ('regresion', Lasso())]),
             param_grid={'polinomial__degree': [2, 3],
                         'regresion__alpha': [0.01, 0.1, 1, 10, 100]},
             scoring='neg_mean_squared_error', verbose=2)

In [15]:
best_model_lasso = grid_search.best_estimator_

pd.DataFrame(grid_search.cv_results_)

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
0     600.466634    115.096062         0.481227        0.066254   
1     440.805827      1.248212         0.438164        0.002499   
2     434.488584      1.900389         0.430388        0.010720   
3     430.213376      2.817915         0.425950        0.012108   
4     372.538636      2.102951         0.435474        0.009408   
5       0.029857      0.004420         0.000000        0.000000   
6       0.031044      0.003259         0.000000        0.000000   
7       0.022968      0.005942         0.000000        0.000000   
8       0.031393      0.007527         0.000000        0.000000   
9       0.027839      0.002559         0.000000        0.000000   

  param_polinomial__degree param_regresion__alpha  \
0                        2                   0.01   
1                        2                    0.1   
2                        2                      1   
3                        2                     10   
4                        2                    100   
5                        3                   0.01   
6                        3                    0.1   
7                        3                      1   
8                        3                     10   
9                        3                    100   

                                              params  split0_test_score  \
0  {'polinomial__degree': 2, 'regresion__alpha': ...        -103.416583   
1  {'polinomial__degree': 2, 'regresion__alpha': ...        -102.667265   
2   {'polinomial__degree': 2, 'regresion__alpha': 1}        -100.982725   
3  {'polinomial__degree': 2, 'regresion__alpha': 10}         -98.291750   
4  {'polinomial__degree': 2, 'regresion__alpha': ...         -95.997563   
5  {'polinomial__degree': 3, 'regresion__alpha': ...                NaN   
6  {'polinomial__degree': 3, 'regresion__alpha': ...                NaN   
7   {'polinomial__degree': 3, 'regresion__alpha': 1}                NaN   
8  {'polinomial__degree': 3, 'regresion__alpha': 10}                NaN   
9  {'polinomial__degree': 3, 'regresion__alpha': ...                NaN   

   split1_test_score  split2_test_score  split3_test_score  split4_test_score  \
0        -131.786461        -108.295748        -110.843473        -101.884848   
1        -128.816274        -107.776144        -110.506929        -102.452255   
2        -128.656651        -107.245433        -109.858964        -103.966837   
3        -114.933034        -104.122888        -106.165090        -108.025224   
4        -104.492004         -96.359931        -102.508110         -95.824411   
5                NaN                NaN                NaN                NaN   
6                NaN                NaN                NaN                NaN   
7                NaN                NaN                NaN                NaN   
8                NaN                NaN                NaN                NaN   
9                NaN                NaN                NaN                NaN   

   mean_test_score  std_test_score  rank_test_score  
0      -111.245423       10.767613                5  
1      -110.443773        9.685117                4  
2      -110.142122        9.729208                3  
3      -106.307597        5.411016                2  
4       -99.036404        3.702196                1  
5              NaN             NaN                6  
6              NaN             NaN                6  
7              NaN             NaN                6  
8              NaN             NaN                6  
9              NaN             NaN                6

In [16]:
grid_search.best_params_

{'polinomial__degree': 2, 'regresion__alpha': 100}

In [23]:
y_pred_train = best_model_lasso.predict(X_train)
y_pred_test = best_model_lasso.predict(X_test)
#y_pred_year =np.round(y_pred_test).astype(int)
y_pred_test

array([2005.702727  , 1992.99700795, 2000.14788477, ..., 1998.32438902,
       1995.37839234, 2003.25465358])

In [18]:
n,p = X_train.shape

print('------------ Regresión Lasso con entrenamiento------------')
print("Residual sum of squares (MSE): %.2f" % mean_squared_error(y_train,y_pred_train))
print("R2-score: %.5f" % r2_score(y_train, y_pred_train) )
print("Adj R2-score: %.5f" % ( 1-(1-r2_score(y_train, y_pred_train))*(n-1)/(n-p-1)) )


------------ Regresión Lasso con entrenamiento------------
Residual sum of squares (MSE): 78.05
R2-score: 0.33224
Adj R2-score: 0.33148


In [19]:
from joblib import dump, load

dump(best_model_lasso,'lasso_regressor.pkl')

['lasso_regressor.pkl']

In [20]:
model_lasso = load('lasso_regressor.pkl') 
model_lasso

Pipeline(steps=[('polinomial', PolynomialFeatures()),
                ('regresion', Lasso(alpha=100))])

In [25]:
df_cv = pd.DataFrame({"Id": range(1, len(y_pred_test)+1), "y":y_pred_test})
df_cv
df_cv.to_csv('lasso_cv2.csv', sep=',', index=False)

### PCA

### Random forest

In [ ]:
# Crea un modelo de Random Forest (ajusta los hiperparámetros según sea necesario)
random_forest = RandomForestClassifier(n_estimators=100, random_state=42)

# Entrena el modelo en el conjunto de entrenamiento
random_forest.fit(X_train, y_train)

RandomForestClassifier(random_state=42)

In [ ]:
y_pred = random_forest.predict(X_test)
y_pred

array([2012, 2006, 2009, ..., 2011, 2011, 2011], dtype=int64)

Grid search random forest

In [ ]:
# Read data
data = pd.read_csv('trainReg.txt')
real_data = pd.read_csv('testReg.txt')

#X_train, y_train = data.drop(['V1', 'V4'], axis= 1), data['Y1'] 
X_real= real_data.drop(['Id', 'V4'], axis= 1)


class Modeloptimization:
    def __init__(self, X_train, X_test, y_train, y_test):
        self.X_train = X_train
        self.X_test = X_test
        self.y_train = y_train
        self.y_test  = y_test
    
    def Obtective(self, trial):
        n_estimators = trial.suggest_int('n_estimators', 100, 200)
        max_depth = trial.suggest_int ('max_depth', 5, 20)

        model = RandomForestRegressor(criterion= 'squared_error', n_estimators= n_estimators, max_depth=max_depth, n_jobs= -1)

        model.fit(self.X_train, self.y_train)

        return model.score(self.X_train, self.y_train)

if __name__ == '__main__':
    x,y = data.drop(['V1', 'V4'], axis= 1), data['V1'] 
    X_train, y_train, X_test, y_test = train_test_split(x, y, test_size= 0.3, random_state=23)
    
    y_test = list()

    model = Modeloptimization(X_train, y_train, X_test, y_test)

    study = optuna.create_study()

    study.optimize(model.Obtective, n_trials=100)

    print(f"best parameters {study.best_params}")
    print(f"best score {study.best_value}")


[I 2023-12-05 13:47:52,809] A new study created in memory with name: no-name-00737f77-edb9-4293-8b85-0f697460d34e
[I 2023-12-05 13:50:17,105] Trial 0 finished with value: 0.5807310472115936 and parameters: {'n_estimators': 133, 'max_depth': 12}. Best is trial 0 with value: 0.5807310472115936.
[I 2023-12-05 13:51:14,423] Trial 1 finished with value: 0.2370336104707882 and parameters: {'n_estimators': 107, 'max_depth': 6}. Best is trial 1 with value: 0.2370336104707882.
[I 2023-12-05 13:53:26,442] Trial 2 finished with value: 0.7510212659736187 and parameters: {'n_estimators': 105, 'max_depth': 15}. Best is trial 1 with value: 0.2370336104707882.
[I 2023-12-05 13:57:43,184] Trial 3 finished with value: 0.8439643884921946 and parameters: {'n_estimators': 176, 'max_depth': 18}. Best is trial 1 with value: 0.2370336104707882.
[I 2023-12-05 14:02:33,883] Trial 4 finished with value: 0.8749250182403218 and parameters: {'n_estimators': 196, 'max_depth': 20}. Best is trial 1 with value: 0.23703

best parameters {'n_estimators': 154, 'max_depth': 5}
best score 0.1999923037162662


In [26]:
Randomreg = RandomForestRegressor(n_estimators=154, max_depth=5 ,random_state=23, n_jobs=-1)

Randomreg.fit(X_train, y_train)

RandomForestRegressor(max_depth=5, n_estimators=154, n_jobs=-1, random_state=23)

In [28]:
y_pred_train_rf = Randomreg.predict(X_train)
y_pred_test_rf = Randomreg.predict(X_test)
#y_pred_year_rf =np.round(y_pred_test_rf).astype(int)
y_pred_test_rf

array([2004.10230435, 2002.47490717, 1993.39331537, ..., 2000.742824  ,
       2006.46731061, 2003.68226842])

In [ ]:
from joblib import dump, load

dump(Randomreg,'Randomforest.pkl')

['Randomforest.pkl']

In [29]:
df_cv = pd.DataFrame({"Id": range(1, len(y_pred_test_rf)+1), "y":y_pred_test_rf})
df_cv
df_cv.to_csv('randomforest.csv', sep=',', index=False)

In [33]:
file = 'C:/Users/danie/OneDrive - Universidad de los andes/Doctorado/Statistical learning/Proyecto/testReg.txt'
data = pd.read_csv(file)
# Guardar el DataFrame en un archivo CSV
data.to_csv('test.csv', index=False)

In [40]:
file = 'C:/Users/danie/OneDrive - Universidad de los andes/Doctorado/Statistical learning/Proyecto/linear_predictions.csv'
data = pd.read_csv(file)
data.head


<bound method NDFrame.head of           Id            y
0          1  2005.211829
1          2  1996.683909
2          3  1998.884263
3          4  2002.927439
4          5  2003.579781
...      ...          ...
18652  18653  2008.756996
18653  18654  2005.876634
18654  18655  2000.538641
18655  18656  1998.265444
18656  18657  2008.601889

[18657 rows x 2 columns]>

## Problema 2 Bankruptcy

Modelos posibles Music year prediction

1. K-vecinos
2. Arboles de desion (boosting y pruning)
3. Butstraping
4. Bagging y Staking
5. Random forest
6. Boosting
7. SVM
8. Regresion logistica
9. Redes neuronales
